In [ ]:
# from sentence_transformers import SentenceTransformer

# model = SentenceTransformer("Alibaba-NLP/gte-Qwen2-1.5B-instruct", trust_remote_code=True)
# # In case you want to reduce the maximum length:
# model.max_seq_length = 8192

# # check vector dimensions
# print(model.get_sentence_embedding_dimension())

In [53]:
import re


def clean_title(title):
    # Extract the authority and the rest of the title
    match = re.match(r'^(?:Rozporządzenie|Obwieszczenie)\s+(.*?)\s+z\s+dnia.*?(?:w sprawie|zmieniające)', title, re.IGNORECASE)
    authority = match.group(1) if match else ""
    
    # Remove the document type, date, and "w sprawie" phrases
    title = title.replace("w sprawie", "dot. ")
    title = re.sub(r'^.*?(?:z dnia \d+\s+\w+\s+\d{4}\s*r\.\s*)', '', title)
    title = re.sub(r'(?:zmieniające\s+rozporządzenie\s+)?w\s+sprawie\s+', '', title)
    title = title.replace("Rzeczypospolitej Polskiej ogłoszenia jednolitego tekstu ustawy", "")
    # Combine authority with cleaned title
    cleaned_title = f"{authority} {title}".strip()
    
    # remove this type of things with (ALPHANUMERICBIGCASENOSPACES)
    # (PLH120079)
    cleaned_title = re.sub(r'\(\w+\d+\)', '', cleaned_title)
    # Remove extra whitespace
    cleaned_title = re.sub(r'\s+', ' ', cleaned_title).strip()
    patterns_to_remove = [
        r"Ministra",
        r"Marszałka Sejmu Rzeczypospolitej Polskiej",
        r"Prezesa Rady Ministrów",
        r"Rady Ministrów",
        r"ogłoszenia jednolitego tekstu",
        r"zmieniające rozporządzenie",
    ]
    for pattern in patterns_to_remove:
        text = re.sub(pattern, "", cleaned_title)
    
    # Convert to lowercase
    text = text.lower()
    
    # Remove special characters and extra whitespace
    text = re.sub(r'[^a-zA-Z0-9\s]', '', text)
    text = re.sub(r'\s+', ' ', text).strip()


    return cleaned_title
text = "Rozporządzenie Ministra Klimatu i Środowiska z dnia 9 grudnia 2022 r. w sprawie funkcjonowania Bazy danych o produktach i opakowaniach oraz o gospodarce odpadami"
clean_title(text)

'Ministra Klimatu i Środowiska dot. funkcjonowania Bazy danych o produktach i opakowaniach oraz o gospodarce odpadami'

In [54]:
# load documents from `acts.csv` `
import pandas as pd

acts = pd.read_csv("acts.csv", nrows=20)
acts['title'] = acts['title'].apply(clean_title)

# to csv
acts.to_csv("acts_cleaned.csv", index=False)


# there is only title column in the csv file
documents = acts["title"].tolist()
print(len(documents))
print(documents[:5])

20
['Ministra Klimatu i Środowiska dot. funkcjonowania Bazy danych o produktach i opakowaniach oraz o gospodarce odpadami', 'Ministra Finansów dot. adnotacji dot. zbiegu egzekucji oraz dokonywania doręczeń przy wykorzystaniu systemu teleinformatycznego albo z użyciem środków komunikacji elektronicznej pomiędzy organami egzekucyjnymi oraz pomiędzy organem egzekucyjnym a komornikiem sądowym', 'Ministra Edukacji i Nauki zmieniające rozporządzenie dot. warunków wynagradzania egzaminatorów za udział w przeprowadzaniu egzaminów oraz nauczycieli akademickich za udział w przeprowadzaniu części ustnej egzaminu maturalnego', 'Ministra Rolnictwa i Rozwoju Wsi dot. wzoru paszportu bydła', 'Ministra Infrastruktury zmieniające rozporządzenie dot. warunków ustalania oraz sposobu dokonywania zwrotu kosztów używania do celów służbowych samochodów osobowych, motocykli i motorowerów niebędących własnością pracodawcy']


In [44]:
from __future__ import annotations
# add this env GOOGLE_APPLICATION_CREDENTIALS = (__file_name).parent / sejm-stats-439117-39efc9d2f8b8.json
os.env()
from vertexai.language_models import TextEmbeddingInput, TextEmbeddingModel
import vertexai


vertexai.init(project="sejm-stats-439117")

def embed_text(texts:list) -> list[list[float]]:
    # A list of texts to be embedded.
    # The dimensionality of the output embeddings.
    dimensionality = 768
    # The task type for embedding. Check the available tasks in the model's documentation.
    task = "RETRIEVAL_DOCUMENT"

    model = TextEmbeddingModel.from_pretrained("text-multilingual-embedding-002")
    inputs = [TextEmbeddingInput(text, task) for text in texts]
    kwargs = dict(output_dimensionality=dimensionality) if dimensionality else {}
    embeddings = model.get_embeddings(inputs, **kwargs)

    print(embeddings)
    # Example response:
    # [[0.006135190837085247, -0.01462465338408947, 0.004978656303137541, ...], [0.1234434666, ...]],
    return [embedding.values for embedding in embeddings]

In [45]:
embeddings = embed_text(documents)
print(len(embeddings[0]))

[TextEmbedding(values=[0.014095100574195385, -0.0022274048533290625, -0.018404202535748482, 0.001826738123781979, 0.0411653108894825, 0.035570062696933746, 0.01163584366440773, 0.03992582485079765, -0.021989615634083748, -0.01650875248014927, -0.03199541196227074, 0.021761346608400345, -0.07232926785945892, -0.05570073798298836, -0.04779164865612984, -0.035547446459531784, 0.024377159774303436, -0.05113290622830391, -0.04490647092461586, 0.05564825236797333, -0.04141571745276451, 0.010320733301341534, 0.05527147278189659, -0.00043978056055493653, -0.02227737568318844, 0.03231293708086014, 0.04303743317723274, -0.08717270195484161, 0.0068199713714420795, 0.07917845994234085, 0.011052732355892658, 0.0362202525138855, -0.016159245744347572, 0.04472459480166435, 0.014806780964136124, -0.04964633658528328, -0.014990627765655518, 0.004246951080858707, -0.017311029136180878, 0.058833979070186615, 0.04257167875766754, 0.0546453520655632, 0.028678923845291138, 0.059103842824697495, -0.034711275

In [60]:
import numpy as np
embeddings = np.array(embeddings)
embeddings.shape

(20, 768)

In [59]:


test = "lekarze apteki pielegniarki"
phrase_embedding = embed_text([test])
phrase_embedding = np.array(phrase_embedding)

[TextEmbedding(values=[-0.010339343920350075, 0.0230109803378582, -0.006553579121828079, 0.017496472224593163, 0.001970481825992465, 0.03842616826295853, -0.019765613600611687, -0.013875403441488743, -0.02730896696448326, -0.017898425459861755, -0.015793684870004654, 0.01893896609544754, -0.03598328307271004, -0.042810577899217606, -0.06031975895166397, -0.03054341860115528, -0.0011370733845978975, -0.08397603034973145, -0.0030810495372861624, 0.09320647269487381, -0.07040853053331375, 0.017201002687215805, 0.0596543587744236, -0.028858786448836327, -0.004011009354144335, 0.04429541528224945, 0.03743739426136017, -0.009160324931144714, 0.0036217335145920515, 0.08054512739181519, 0.008424599654972553, 0.07786509394645691, -0.006623266730457544, -0.007184586953371763, 0.0009791019838303328, -0.029494138434529305, -0.002708379179239273, -0.010167955420911312, 0.002295803977176547, 0.1038985550403595, 0.03144686296582222, 0.00924631580710411, 0.030454620718955994, 0.061332762241363525, 0.0

In [61]:
from sklearn.metrics.pairwise import cosine_similarity

similarities = cosine_similarity(phrase_embedding, embeddings)

# Get the indices of the top 5 most similar documents
top_5_indices = similarities[0].argsort()[-5:][::-1]

# Print the top 5 most similar documents and their similarity scores
for index in top_5_indices:
    print(documents[index])
    print(similarities[0][index])

Ministra Zdrowia zmieniające rozporządzenie dot. recept
0.8805070375914138
Ministra Klimatu i Środowiska zmieniające rozporządzenie dot. wzoru oświadczenia odbiorcy uprawnionego
0.7627699227145643
Ministra Klimatu i Środowiska dot. funkcjonowania Bazy danych o produktach i opakowaniach oraz o gospodarce odpadami
0.7584921434561185
Ministra Klimatu i Środowiska dot. specjalnego obszaru ochrony siedlisk Mieszkowicka Dąbrowa
0.7369849093878879
Ministra Rolnictwa i Rozwoju Wsi dot. szczegółowego zakresu informacji zawartych w komputerowej bazie danych
0.7323576730556582
